In [1]:
import pandas as pd

df = pd.read_csv('data/train_pp.csv')
test_df = pd.read_csv('data/test_pp.csv')

X = df.drop(['accident_risk', 'id'], axis=1)
y = df['accident_risk']

In [2]:
def submission_generator(trained_model):
    test_df_preprocessed = test_df.drop('id', axis=1)
    return pd.concat([test_df['id'], pd.Series(trained_model.predict(test_df_preprocessed))], axis=1).rename({0: 'accident_risk'}, axis=1)

In [3]:
import optuna
from xgboost import XGBRegressor
from sklearn.model_selection import KFold
from sklearn.metrics import root_mean_squared_error
import numpy as np 

### XGB

In [22]:
kf = KFold(5, shuffle=True)

def objective(trials):
    max_leaves = trials.suggest_int('max_leaves', 0, 256)
    max_depth = trials.suggest_int('max_depth', 2, 512)
    learning_rate = trials.suggest_float('learning_rate', 0.003, 0.3)
    n_estimators = trials.suggest_int('n_estimators', 24, 1024)

    subsample = trials.suggest_float('subsample', 0.1, 1)
    colsample_bytree = trials.suggest_float('colsample_bytree', 0.1, 1)

    rmses = []
    for train_index, test_index in kf.split(X):
        clf = XGBRegressor(
            max_leaves=max_leaves,
            max_depth=max_depth,
            learning_rate=learning_rate,
            n_estimators=n_estimators,
            device='cuda',
            subsample=subsample,
            colsample_bytree=colsample_bytree,
        )
        X_train = X.iloc[train_index]
        y_train = y.iloc[train_index]
        X_test = X.iloc[test_index]
        y_test = y.iloc[test_index]

        clf.fit(X_train, y_train)
        y_pred = clf.predict(X_test)

        rmse = root_mean_squared_error(y_pred, y_test)
        rmses.append(rmse)

    return np.mean(rmses)

In [23]:
xgb_study = optuna.create_study()
xgb_study.optimize(objective, n_trials=50)

[I 2025-10-24 22:49:45,651] A new study created in memory with name: no-name-26cc668b-c6ff-4835-a2b9-82db7f6c987e
[I 2025-10-24 22:49:47,045] Trial 0 finished with value: 0.056054882006762494 and parameters: {'max_leaves': 119, 'max_depth': 449, 'learning_rate': 0.241918760799226, 'n_estimators': 62}. Best is trial 0 with value: 0.056054882006762494.
[W 2025-10-24 22:49:52,917] Trial 1 failed with parameters: {'max_leaves': 134, 'max_depth': 365, 'learning_rate': 0.13955529461031632, 'n_estimators': 989} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "/home/woxane/anaconda3/lib/python3.10/site-packages/optuna/study/_optimize.py", line 201, in _run_trial
    value_or_values = func(trial)
  File "/tmp/ipykernel_16606/1306643608.py", line 24, in objective
    clf.fit(X_train, y_train)
  File "/home/woxane/anaconda3/lib/python3.10/site-packages/xgboost/core.py", line 774, in inner_f
    return func(**kwargs)
  File "/home/woxane/anaconda3/lib

KeyboardInterrupt: 

In [37]:
clf_xgb = XGBRegressor(
    max_leaves= 76,
    max_depth=7,
    learning_rate=0.030293475264037178,
    n_estimators=721,
    device='cuda',
)
clf_xgb.fit(X, y)

submission = submission_generator(clf_xgb)
submission.to_csv('XGB_meta_optuna.csv', index=False)

In [13]:
xgb_study.best_params

{'max_leaves': 76,
 'max_depth': 7,
 'learning_rate': 0.030293475264037178,
 'n_estimators': 721}

### LGBM

In [4]:
from lightgbm import LGBMRegressor
from sklearn.model_selection import KFold
from sklearn.metrics import root_mean_squared_error

In [7]:
kf = KFold(5, shuffle=True)

def objective(trials):
    num_leaves = trials.suggest_int('num_leaves', 4, 256)
    max_depth = trials.suggest_int('max_depth', -1, 512)
    learning_rate = trials.suggest_float('learning_rate', 0.003, 0.3)
    n_estimators = trials.suggest_int('n_estimatora', 24, 1024)

    subsample = trials.suggest_float('subsample', 0.1, 1)
    colsample_bytree = trials.suggest_float('colsample_bytree', 0.1, 1)

    rmses = []
    for train_index, test_index in kf.split(X):
        clf = LGBMRegressor(
            num_leaves=num_leaves,
            max_depth=max_depth,
            learning_rate=learning_rate,
            n_estimators=n_estimators,
            subsample=subsample,
            colsample_bytree=colsample_bytree,
        )
        
        X_train = X.iloc[train_index]
        y_train = y.iloc[train_index]
        X_test = X.iloc[test_index]
        y_test = y.iloc[test_index]

        clf.fit(X_train, y_train)
        y_pred = clf.predict(X_test)

        rmse = root_mean_squared_error(y_pred, y_test)
        rmses.append(rmse)

    return np.mean(rmses)

In [8]:
lgbm_study = optuna.create_study()
lgbm_study.optimize(objective, n_trials=200)

[I 2025-10-25 22:51:49,524] A new study created in memory with name: no-name-0d2c5962-98dc-402b-bd99-fb2bfb574b32


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004227 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 430
[LightGBM] [Info] Number of data points in the train set: 414203, number of used features: 17
[LightGBM] [Info] Start training from score 0.352372
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003207 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 429
[LightGBM] [Info] Number of data points in the train set: 414203, number of used features: 17
[LightGBM] [Info] Start training from score 0.352381
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003228 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enoug

[I 2025-10-25 22:52:07,746] Trial 0 finished with value: 0.05615959443485559 and parameters: {'num_leaves': 209, 'max_depth': 95, 'learning_rate': 0.04136725187551821, 'n_estimatora': 868, 'subsample': 0.40424473334349453, 'colsample_bytree': 0.9050835061876163}. Best is trial 0 with value: 0.05615959443485559.


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001360 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 429
[LightGBM] [Info] Number of data points in the train set: 414203, number of used features: 17
[LightGBM] [Info] Start training from score 0.352255
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain:

[I 2025-10-25 22:52:18,403] Trial 1 finished with value: 0.056194547459120225 and parameters: {'num_leaves': 130, 'max_depth': 59, 'learning_rate': 0.21197165830363832, 'n_estimatora': 643, 'subsample': 0.7484949858579731, 'colsample_bytree': 0.1867397012909353}. Best is trial 0 with value: 0.05615959443485559.


...

[I 2025-10-25 23:26:11,095] Trial 197 finished with value: 0.055997016221005766 and parameters: {'num_leaves': 75, 'max_depth': 451, 'learning_rate': 0.047979417922212386, 'n_estimatora': 803, 'subsample': 0.5894951487059287, 'colsample_bytree': 0.630429727222546}. Best is trial 182 with value: 0.05598720777174861.


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002201 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 425
[LightGBM] [Info] Number of data points in the train set: 414203, number of used features: 17
[LightGBM] [Info] Start training from score 0.352425
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003271 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 435
[LightGBM] [Info] Number of data points in the train set: 414203, number of used features: 17
[LightGBM] [Info] Start training from score 0.352379
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002421 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enoug

[I 2025-10-25 23:26:22,498] Trial 198 finished with value: 0.05604976120163081 and parameters: {'num_leaves': 82, 'max_depth': 456, 'learning_rate': 0.06551642182802789, 'n_estimatora': 790, 'subsample': 0.5646217686675808, 'colsample_bytree': 0.5640424068579456}. Best is trial 182 with value: 0.05598720777174861.


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.006355 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 430
[LightGBM] [Info] Number of data points in the train set: 414203, number of used features: 17
[LightGBM] [Info] Start training from score 0.352265
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003528 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 429
[LightGBM] [Info] Number of data points in the train set: 414203, number of used features: 17
[LightGBM] [Info] Start training from score 0.352347
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003821 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enoug

[I 2025-10-25 23:26:32,458] Trial 199 finished with value: 0.05600239951944967 and parameters: {'num_leaves': 73, 'max_depth': 444, 'learning_rate': 0.04673070436639924, 'n_estimatora': 706, 'subsample': 0.28478784922225675, 'colsample_bytree': 0.6618265298334267}. Best is trial 182 with value: 0.05598720777174861.


In [10]:
clf_lgbm = LGBMRegressor(**lgbm_study.best_params)
clf_lgbm.fit(X, y)

submission = submission_generator(clf_lgbm)
submission.to_csv('LGBM_meta_optuna.csv', index=False)

[LightGBM] [Warning] Unknown parameter: n_estimatora
[LightGBM] [Warning] Unknown parameter: n_estimatora
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003528 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 432
[LightGBM] [Info] Number of data points in the train set: 517754, number of used features: 17
[LightGBM] [Info] Start training from score 0.352377
[LightGBM] [Warning] Unknown parameter: n_estimatora


In [11]:
lgbm_study.best_params

{'num_leaves': 66,
 'max_depth': 449,
 'learning_rate': 0.03502441310895256,
 'n_estimatora': 820,
 'subsample': 0.592592101509771,
 'colsample_bytree': 0.6862792428425046}

### SGD

In [14]:
from sklearn.model_selection import KFold
from sklearn.metrics import root_mean_squared_error
from sklearn.linear_model import SGDRegressor

In [34]:
kf = KFold(5, shuffle=True)

def object(trial):
    penalty = trial.suggest_categorical('penalty', ['l1', 'l2', 'elasticnet', None])
    alpha = trial.suggest_float('alpha', 0.0, 10) # It could goes to inf, but i choose 10 at the high

    # l1 ratio used only when penalty is elastic_net
    l1_ratio = trial.suggest_float('l1_ratio', 0.0, 1)
    
    rmses = []
    
    for train_index, test_index in kf.split(X):
        sgd_model = SGDRegressor(
            penalty=penalty,
            alpha=alpha,
            l1_ratio=l1_ratio,
        )
        
        X_train = X.iloc[train_index]
        y_train = y.iloc[train_index]
        X_test = X.iloc[test_index]
        y_test = y.iloc[test_index]

        sgd_model.fit(X_train, y_train)
        y_pred = sgd_model.predict(X_test)

        rmse = root_mean_squared_error(y_pred, y_test)
        rmses.append(rmse)

    return np.mean(rmses)                           

In [36]:
sgd_study = optuna.create_study()
sgd_study.optimize(object, n_trials=50)

[I 2025-10-25 18:08:28,130] A new study created in memory with name: no-name-613fc532-8345-482a-a07f-801ef4481f91
[I 2025-10-25 18:09:10,899] Trial 0 finished with value: 0.166416122669707 and parameters: {'penalty': 'l1', 'alpha': 4.908082094838901, 'l1_ratio': 0.01988816843082708}. Best is trial 0 with value: 0.166416122669707.
[I 2025-10-25 18:09:14,990] Trial 1 finished with value: 0.1664408041703944 and parameters: {'penalty': 'elasticnet', 'alpha': 3.010212094599235, 'l1_ratio': 0.7006586370510401}. Best is trial 0 with value: 0.166416122669707.
[I 2025-10-25 18:09:19,074] Trial 2 finished with value: 0.16642249662660127 and parameters: {'penalty': 'elasticnet', 'alpha': 8.390161778778516, 'l1_ratio': 0.2699618168043416}. Best is trial 0 with value: 0.166416122669707.
[I 2025-10-25 18:10:09,660] Trial 3 finished with value: 0.09344806420635911 and parameters: {'penalty': None, 'alpha': 4.885411915624238, 'l1_ratio': 0.26027172202708904}. Best is trial 3 with value: 0.093448064206

In [39]:
sgd_model = SGDRegressor(**sgd_study.best_params)
sgd_model.fit(X, y)

submission = submission_generator(sgd_model)
submission.to_csv('SGD_meta_optuna.csv', index=False)

In [41]:
sgd_study.best_params

{'penalty': None, 'alpha': 4.223601774273774, 'l1_ratio': 0.8940821225850496}

### Bayesian Ridge

In [43]:
from sklearn.model_selection import KFold
from sklearn.metrics import root_mean_squared_error
from sklearn.linear_model import BayesianRidge

In [71]:
kf = KFold(5, shuffle=True)

def object(trial):
    alpha_1 = trial.suggest_float('alpha_1', 1e-9, 0.1)
    alpha_2 = trial.suggest_float('alpha_2', 1e-9, 0.1)

    lambda_1 = trial.suggest_float('lambda_1', 1e-9, 0.1)
    lambda_2 = trial.suggest_float('lambda_2', 1e-9, 0.1)
    
    rmses = []
    
    for train_index, test_index in kf.split(X):
        bayes_ridge_model = BayesianRidge(
            alpha_1=alpha_1,
            alpha_2=alpha_2,
            lambda_1=lambda_1,
            lambda_2=lambda_2,
        )
        
        X_train = X.iloc[train_index]
        y_train = y.iloc[train_index]
        X_test = X.iloc[test_index]
        y_test = y.iloc[test_index]

        bayes_ridge_model.fit(X_train, y_train)
        y_pred = bayes_ridge_model.predict(X_test)

        rmse = root_mean_squared_error(y_pred, y_test)
        rmses.append(rmse)

    return np.mean(rmses)                           

In [75]:
bayes_ridge_study = optuna.create_study()
bayes_ridge_study.optimize(object, n_trials=500)

[I 2025-10-25 18:55:26,525] A new study created in memory with name: no-name-c1f9ae31-03b8-4d36-a386-229f562f1442
[I 2025-10-25 18:55:27,445] Trial 0 finished with value: 0.05803608314192469 and parameters: {'alpha_1': 0.0027820554309947085, 'alpha_2': 0.027057090724225158, 'lambda_1': 0.02932973344190304, 'lambda_2': 0.059382990753758025}. Best is trial 0 with value: 0.05803608314192469.
[I 2025-10-25 18:55:28,331] Trial 1 finished with value: 0.0580357203043565 and parameters: {'alpha_1': 0.011904303051045655, 'alpha_2': 0.060819179327497266, 'lambda_1': 0.02647636002323545, 'lambda_2': 0.006389700031191174}. Best is trial 1 with value: 0.0580357203043565.
[I 2025-10-25 18:55:29,185] Trial 2 finished with value: 0.05803612238628429 and parameters: {'alpha_1': 0.06673138805996898, 'alpha_2': 0.02574268981832068, 'lambda_1': 0.0897329481930369, 'lambda_2': 0.011256628575987391}. Best is trial 1 with value: 0.0580357203043565.
[I 2025-10-25 18:55:30,105] Trial 3 finished with value: 0.0

In [85]:
bayes_ridge_model = BayesianRidge(**bayes_ridge_study.best_params)
bayes_ridge_model.fit(X, y)

submission = submission_generator(bayes_ridge_model)
submission.to_csv('bayes_ridge_meta_optuna.csv', index=False)

In [87]:
bayes_ridge_study.best_params

{'alpha_1': 0.012972867153230679,
 'alpha_2': 0.03937728242649084,
 'lambda_1': 5.3000736672220825e-06,
 'lambda_2': 0.07761015011781103}

### KNN

In [90]:
from sklearn.neighbors import KNeighborsRegressor
from sklearn.model_selection import KFold
from sklearn.metrics import root_mean_squared_error

In [98]:
kf = KFold(5, shuffle=True)

def objective(trial):
    n_neighbors = trial.suggest_int('n_neighbors', 2, 700)
    weights = trial.suggest_categorical('weights', ['uniform', 'distance'])
    # Minkowski P
    p = trial.suggest_int('p', 1, 10)
    
    rmses = []
    
    for train_index, test_index in kf.split(X):
        knn_model = KNeighborsRegressor(
            n_neighbors=n_neighbors,
            weights=weights,
            p=p,
        )
        
        X_train = X.iloc[train_index]
        y_train = y.iloc[train_index]
        X_test = X.iloc[test_index]
        y_test = y.iloc[test_index]

        knn_model.fit(X_train, y_train)
        y_pred = knn_model.predict(X_test)

        rmse = root_mean_squared_error(y_pred, y_test)
        rmses.append(rmse)

    return np.mean(rmses)                           

In [ ]:
knn_study = optuna.create_study()
knn_study.optimize(objective, n_trials=2)

[I 2025-10-25 19:15:57,373] A new study created in memory with name: no-name-5839a9f3-7bff-4923-9cb0-a6189dbd2fdc


In [ ]:
knn_study.best_parameters

### Catboost

In [12]:
from catboost import CatBoostRegressor
from sklearn.model_selection import KFold
from sklearn.metrics import root_mean_squared_error

In [27]:
kf = KFold(5, shuffle=True)

def objective(trial):
    learning_rate = trial.suggest_float('learning_rate', 0.001, 0.03)
    depth = trial.suggest_int('depth', 2, 16)
    l2_leaf_reg = trial.suggest_float('l2_leaf_reg', 0.0, 10) # it could be goes to infinite but i choose ten for the maximum
    random_strength = trial.suggest_float('random_strength', 0, 1) # IDK about this
    bagging_temperature = trial.suggest_float('bagging_temperature', 0, 10) # it goes to infinite

    rmses = []
    
    for train_index, test_index in kf.split(X):
        cat_model = CatBoostRegressor(
            learning_rate=learning_rate,
            depth=depth,
            l2_leaf_reg=l2_leaf_reg,
            random_strength=random_strength,
            bagging_temperature=bagging_temperature,
            task_type='GPU',
        )
        
        X_train = X.iloc[train_index]
        y_train = y.iloc[train_index]
        X_test = X.iloc[test_index]
        y_test = y.iloc[test_index]

        cat_model.fit(X_train, y_train)
        y_pred = cat_model.predict(X_test)

        rmse = root_mean_squared_error(y_pred, y_test)
        rmses.append(rmse)

    return np.mean(rmses)                           

In [ ]:
cat_study = optuna.create_study()
cat_study.optimize(objective, n_trials=50)

[I 2025-10-25 23:34:25,250] A new study created in memory with name: no-name-24f75fa1-206b-4fbc-8543-2405635db9b5


0:	learn: 0.1646384	total: 42.8ms	remaining: 42.7s
1:	learn: 0.1629984	total: 85.9ms	remaining: 42.8s
2:	learn: 0.1612624	total: 127ms	remaining: 42.2s
3:	learn: 0.1595599	total: 168ms	remaining: 41.8s
4:	learn: 0.1579529	total: 210ms	remaining: 41.9s
5:	learn: 0.1563106	total: 251ms	remaining: 41.6s
6:	learn: 0.1546732	total: 289ms	remaining: 41s
7:	learn: 0.1530796	total: 326ms	remaining: 40.4s
8:	learn: 0.1514969	total: 362ms	remaining: 39.9s
9:	learn: 0.1498830	total: 396ms	remaining: 39.2s
10:	learn: 0.1483482	total: 430ms	remaining: 38.7s
11:	learn: 0.1468506	total: 465ms	remaining: 38.3s
12:	learn: 0.1454298	total: 502ms	remaining: 38.1s
13:	learn: 0.1439275	total: 535ms	remaining: 37.7s
14:	learn: 0.1425165	total: 571ms	remaining: 37.5s
15:	learn: 0.1410683	total: 605ms	remaining: 37.2s
16:	learn: 0.1397010	total: 641ms	remaining: 37.1s
17:	learn: 0.1383163	total: 675ms	remaining: 36.8s
18:	learn: 0.1370289	total: 715ms	remaining: 36.9s
19:	learn: 0.1356881	total: 752ms	remaini

[I 2025-10-25 23:37:57,213] Trial 0 finished with value: 0.05819912153812394 and parameters: {'learning_rate': 0.012938347169589571, 'depth': 14, 'l2_leaf_reg': 6.882357299799528, 'random_strength': 0.9527714839752062, 'bagging_temperature': 9.03381167239618}. Best is trial 0 with value: 0.05819912153812394.


0:	learn: 0.1657554	total: 1.89ms	remaining: 1.89s
1:	learn: 0.1651001	total: 3.51ms	remaining: 1.75s
2:	learn: 0.1644490	total: 5.15ms	remaining: 1.71s
3:	learn: 0.1638028	total: 6.78ms	remaining: 1.69s
4:	learn: 0.1631593	total: 8.43ms	remaining: 1.68s
5:	learn: 0.1625198	total: 10ms	remaining: 1.66s
6:	learn: 0.1618793	total: 11.6ms	remaining: 1.65s
7:	learn: 0.1612468	total: 13.3ms	remaining: 1.65s
8:	learn: 0.1606150	total: 14.9ms	remaining: 1.64s
9:	learn: 0.1599888	total: 16.5ms	remaining: 1.63s
10:	learn: 0.1593650	total: 18.1ms	remaining: 1.63s
11:	learn: 0.1587448	total: 19.7ms	remaining: 1.62s
12:	learn: 0.1581300	total: 21.3ms	remaining: 1.62s
13:	learn: 0.1575177	total: 23ms	remaining: 1.62s
14:	learn: 0.1569059	total: 24.6ms	remaining: 1.62s
15:	learn: 0.1562985	total: 26.2ms	remaining: 1.61s
16:	learn: 0.1556955	total: 27.8ms	remaining: 1.61s
17:	learn: 0.1550952	total: 29.4ms	remaining: 1.6s
18:	learn: 0.1544968	total: 31ms	remaining: 1.6s
19:	learn: 0.1538994	total: 32

[I 2025-10-25 23:38:08,403] Trial 1 finished with value: 0.057247409898424736 and parameters: {'learning_rate': 0.004699273651132039, 'depth': 6, 'l2_leaf_reg': 6.596458294715611, 'random_strength': 0.745011687877708, 'bagging_temperature': 5.2672892918119665}. Best is trial 1 with value: 0.057247409898424736.


...

Exception ignored in: '_catboost._WriteLog'
Traceback (most recent call last):
  File "/home/woxane/anaconda3/lib/python3.10/site-packages/ipykernel/iostream.py", line 655, in write
    def write(self, string: str) -> Optional[int]:  # type:ignore[override]
KeyboardInterrupt: 


19:	learn: 0.1153568	total: 211ms	remaining: 10.3s
20:	learn: 0.1134746	total: 224ms	remaining: 10.4s
21:	learn: 0.1116358	total: 235ms	remaining: 10.4s
22:	learn: 0.1098519	total: 247ms	remaining: 10.5s
23:	learn: 0.1081571	total: 258ms	remaining: 10.5s
24:	learn: 0.1064840	total: 269ms	remaining: 10.5s
25:	learn: 0.1048274	total: 280ms	remaining: 10.5s
26:	learn: 0.1032392	total: 291ms	remaining: 10.5s
27:	learn: 0.1016757	total: 301ms	remaining: 10.4s
28:	learn: 0.1001887	total: 312ms	remaining: 10.4s
29:	learn: 0.0987352	total: 322ms	remaining: 10.4s
30:	learn: 0.0973267	total: 333ms	remaining: 10.4s
31:	learn: 0.0959369	total: 343ms	remaining: 10.4s
32:	learn: 0.0945787	total: 354ms	remaining: 10.4s
33:	learn: 0.0932832	total: 365ms	remaining: 10.4s
34:	learn: 0.0920449	total: 375ms	remaining: 10.3s
35:	learn: 0.0908393	total: 386ms	remaining: 10.3s
36:	learn: 0.0896508	total: 396ms	remaining: 10.3s
37:	learn: 0.0885082	total: 407ms	remaining: 10.3s
38:	learn: 0.0874108	total: 418

KeyboardInterrupt: 

Exception ignored in: '_catboost._WriteLog'
Traceback (most recent call last):
  File "/home/woxane/anaconda3/lib/python3.10/site-packages/ipykernel/iostream.py", line 655, in write
    def write(self, string: str) -> Optional[int]:  # type:ignore[override]
KeyboardInterrupt: 


355:	learn: 0.0553052	total: 4.32s	remaining: 7.82s
356:	learn: 0.0552985	total: 4.33s	remaining: 7.81s
357:	learn: 0.0552922	total: 4.35s	remaining: 7.8s
358:	learn: 0.0552865	total: 4.36s	remaining: 7.79s
359:	learn: 0.0552826	total: 4.38s	remaining: 7.78s
360:	learn: 0.0552765	total: 4.39s	remaining: 7.77s
361:	learn: 0.0552718	total: 4.4s	remaining: 7.76s
362:	learn: 0.0552664	total: 4.41s	remaining: 7.75s
363:	learn: 0.0552620	total: 4.42s	remaining: 7.73s
364:	learn: 0.0552570	total: 4.44s	remaining: 7.72s
365:	learn: 0.0552509	total: 4.45s	remaining: 7.71s
366:	learn: 0.0552473	total: 4.46s	remaining: 7.7s
367:	learn: 0.0552412	total: 4.47s	remaining: 7.68s
368:	learn: 0.0552371	total: 4.49s	remaining: 7.67s
369:	learn: 0.0552314	total: 4.5s	remaining: 7.66s
370:	learn: 0.0552280	total: 4.51s	remaining: 7.65s
371:	learn: 0.0552212	total: 4.52s	remaining: 7.63s
372:	learn: 0.0552148	total: 4.53s	remaining: 7.62s
373:	learn: 0.0552076	total: 4.55s	remaining: 7.61s
374:	learn: 0.05

In [ ]:
cat_model = CatBoostRegressor(**cat_study.best_params)

In [ ]:
cat_study.best_params